In [3]:
import json
import re

In [19]:
import re

def extract_text_sections(text, tag = "###"):
    # Dynamic regex to match any section between ### tags and extract their content
    pattern = tag
    pattern = tag + r"\s*(.*?)\s*:(.*?)\n(?=" + tag + r"|$)"
    matches = re.findall(pattern, text, re.DOTALL)

    result = dict()
    if not matches:
        return result

    # Parse matches into a dictionary
    for key, value in matches:
        result[key.strip().lower().replace(" ", "_")] = value.strip() if value.strip() else None

    return result

# Test cases
def test_extract_text_sections():
    # Test with valid text
    text_valid = """
### Demo no text (return None):

### Decision: 
This is the decision text.

### Reasoning:
This is the reasoning text.

### SQL Query:
SELECT * FROM table;

### Demo no text (return None):
"""
    expected_output = {
        "demo_no_text_(return_none)": None,
        "decision": "This is the decision text.",
        "reasoning": "This is the reasoning text.",
        "sql_query": "SELECT * FROM table;"
    }
#     assert extract_text_sections(text_valid) == expected_output

#     # Test with missing text (should return demo_no_text_return_none as None)
#     text_invalid = """
# ### Demo no text (return None):
# """
#     assert extract_text_sections(text_invalid) == {"demo_no_text_return_none": None}

#     print("All tests passed.")

    return extract_text_sections(text_valid)

# Run the tests
test_extract_text_sections()

{'demo_no_text_(return_none)': None,
 'decision': 'This is the decision text.',
 'reasoning': 'This is the reasoning text.',
 'sql_query': 'SELECT * FROM table;'}

In [14]:
questions = dict()
cal_reasoning = 0
with open('../data/gpt-4o-mini__v3.jsonl') as f:
    for line in f:
        data = json.loads(line)
        ids = data['ids']
        questions[ids] = data
        if 'reasoning' in data:
            cal_reasoning += 1
cal_reasoning

1765

In [15]:
len(questions)

1765

In [16]:
with open('../data/meta-llama__Llama-3.3-70B-Instruct-Turbo-scored-gpt-4o-mini__v3.jsonl') as f:
    for line in f:
        data = json.loads(line)
        ids = data['ids']
        if 'score' not in questions[ids]:
            questions[ids]['score'] = []
        questions[ids]['score'].append(data['score'])

with open('../data/gemini-1.5-flash-scored-gpt-4o-mini__v3.jsonl') as f:
    for line in f:
        data = json.loads(line)
        ids = data['ids']
        if 'score' not in questions[ids]:
            questions[ids]['score'] = []
        questions[ids]['score'].append(data['score'])

with open('../data/gpt-4o-mini-scored-gpt-4o-mini__v3.jsonl') as f:
    for line in f:
        data = json.loads(line)
        ids = data['ids']
        if 'score' not in questions[ids]:
            questions[ids]['score'] = []
        questions[ids]['score'].append(data['score'])

In [17]:
len_sql = 0
for ids, data in questions.items():
    if 'score' in data:
        data['avg'] = sum(data['score']) / 3 # len(data['score'])
    len_sql += len(data['sql'])
len_sql /= len(questions)
len_sql


0.9949008498583569

In [18]:
good_ids = set()
for ids, data in questions.items():
    if 'score' in data and data['avg'] == 1:
        good_ids.add(ids)
        if len(data['sql']) > 1:
            print(ids, data)

In [19]:
len(good_ids)

879

In [20]:
with open('../data/gpt-4o-mini__v3_good.jsonl', 'w') as f:
    for ids, data in questions.items():
        if ids in good_ids:
            f.write(json.dumps(data) + '\n')

In [13]:
count_result_format = 0
good_result_format = 0
for ids, data in questions.items():
    if 'result format' in data['reasoning'].lower():
        count_result_format += 1
        if '### Result Format' in data['reasoning']:
            good_result_format += 1
            print(ids, data['reasoning'])
            break
count_result_format, good_result_format

(0, 0)

In [10]:
for ids, data in questions.items():
  if ids == '74710a9c-1b03-4821-b306-61057c8200cf':
    print('QUESTION ===========')
    print(data['question'])  
    print('TABLES ===========')
    print(data['table'])
    print('ANSWERS ===========')
    print(data['reasoning'])
    print('AVG ===========')
    print(data['avg'])
    break

QUESTION ===========
In Q2 2024, analyze the accounts receivable turnover and days sales outstanding (DSO) for FPT, Vingroup (VIC), and Masan Group (MSN). How do these metrics reflect their collection efficiency, and how might their subsidiaries/investments affect these figures?
TABLES ===========
**Company Info**

| stock_code   | company_name                   | en_company_name              | industry               |
|:-------------|:-------------------------------|:-----------------------------|:-----------------------|
| FPT          | Công ty Cổ phần FPT            | FPT Corporation              | Information Technology |
| MSN          | Công ty Cổ phần Tập đoàn Masan | Masan Group Corporation      | Food and Beverages     |
| VIC          | Tập đoàn Vingroup - Công ty CP | VinGroup Joint Stock Company | Real Estate            |

**category_code_ratio**

| ratio_code   | ratio_name                 |
|:-------------|:---------------------------|
| RTSR         | Receivables To Sal

In [1]:
import random
import json

In [2]:
random.randint(0, 1)

1

In [4]:
import tiktoken

def count_tokens(text: str, model: str = "gpt-4") -> int:
    # Select the tokenizer for the model
    encoding = tiktoken.encoding_for_model(model)
    tokens = encoding.encode(text)
    return len(tokens)

err = 0
total_tokens = 0
num = 1
s = 0
u = 0
a = 0
with open('../data/message_gpt-4o-mini__v4_good.jsonl') as f:
    for line in f:
        try:
            data = json.loads(line)

            with open('../data/message_gpt-4o-mini__v4_good_good.jsonl', 'a') as f:
                json.dump(data, f)
                f.write('\n')

            for message in data:
                text = message['content']
                total_tokens += count_tokens(text)
                if message['role'] == 'system':
                    s += count_tokens(text)
                elif message['role'] == 'user':
                    u += count_tokens(text)
                else:
                    a += count_tokens(text)
        except Exception as e:
            err += 1
        num += 1
total_tokens, err, u, s, a

(1900722, 24, 670171, 1120212, 110339)

In [6]:
with open('../data/message_gpt-4o-mini__v3_good.jsonl') as f:
    for line in f:
        try:
            data = json.loads(line)
            new_data = []
            for message in data:
                role = message['role']
                content = message['content'].strip()
                new_data.append({'role': role, 'content': content})
            with open('../data/message_gpt-4o-mini__v3_good_good.jsonl', 'a') as f:
                json.dump(new_data, f)
                f.write('\n')
                

        except Exception as e:
            print(e)

## Grade Cell

In [16]:
import json

evaluate_path = '../data/gpt-4o-mini-evaluate-gpt-4o-mini__sql_v0.jsonl'
mcq_path = '../data/mcq_v0.jsonl'

evaluate = dict()
cant_ansewer = 0
score = 0

total_questions = 0
with open(mcq_path) as f:
    for line in f:
        data = json.loads(line)
        total_questions += 1


with open(evaluate_path) as f:
    for line in f:
        data = json.loads(line)
        evaluate[data['ids']] = data
        if 'score' in data:
            score += data['score']
        if 'cant_answer' in data and data['cant_answer']:
            cant_ansewer += 1

total_questions, cant_ansewer, score, score/len(evaluate), score/total_questions

(423, 110, 274, 0.6539379474940334, 0.6477541371158393)

In [15]:
sql_path = '../data/deepseek-chat__v0_good.jsonl'
new_sql_path = '../data/sql_v0.jsonl'

with open(sql_path) as f:
    for line in f:
        data = json.loads(line)
        ids = data['ids']
        if evaluate.get(ids, dict()).get('score', 0) == 1:
            with open(new_sql_path, 'a') as f:
                json.dump(data, f)
                f.write('\n')

In [14]:
new_mcq_path = '../data/mcq_v0.jsonl'
with open(mcq_path) as f:
    for line in f:
        data = json.loads(line)
        ids = data['ids']
        if evaluate.get(ids, dict()).get('score', 0) == 1:
            with open(new_mcq_path, 'a') as f:
                json.dump(data, f)
                f.write('\n')


In [8]:
def is_npl(question: dict):
    if 'non-per' in question['question'].lower() and 'bdr' not in question['reasoning'].lower():
        return True
    return False


def contain_en_company(question: dict):
    if 'yoy' in question['reasoning'].lower() and 'quarter = 0' not in question['reasoning'].lower():
        return True
    return False

def contain_data(question, data):
    if data in question['reasoning'].lower():
        return True
    return False

In [11]:
file_path = '../data/gpt-4o-mini__v5.jsonl'
new_file_path = '../data/gpt-4o-mini__v5_2.jsonl'

In [14]:
import json
err = 0

err_id = ''


with open(file_path) as f:
    for line in f:
        data = json.loads(line)
        if contain_data(data, 'average'):
            err += 1
            err_id = data['ids']
        else:
            print('======== QUESTION ===========')
            print(data['question'])  
            print('======== TABLES ===========')
            print(data['table'])
            print('======== ANSWERS ===========')
            print(data['reasoning'])
            # print('AVG ===========')
            # print(data['avg'])
        #     break
        # else:
        #     with open(new_file_path, 'a') as f:
        #         json.dump(data, f)
        #         f.write('\n')

======== QUESTION ===========
What was the Total asset value of Vietcombank (VCB) compared to BIDV (BID) in 2022?
======== TABLES ===========
**Company Info**

| stock_code | en_company_name | industry |
| --- | --- | --- |
| BID | Joint Stock Commercial Bank for Investment and Development of Vietnam | Banking |
| VCB | Joint Stock Commercial Bank For Foreign Trade Of Vietnam | Banking |


**category_code_mapping**

List of category_code with corresponding en_caption
- BS_270: (Balance sheet) TOTAL ASSETS


** SQL 1 Result: financial_statement**

| stock_code | year | quarter | category_code | data |
| --- | --- | --- | --- | --- |
| BID | 2022 | 0 | BS_270 | 2120676711.0 |
| VCB | 2022 | 0 | BS_270 | 1813815170.0 |



======== ANSWERS ===========
To answer the query about the Total asset value of Vietcombank (VCB) compared to BIDV (BID) in 2022, we will follow these steps:

1. Identify the `category_code` for Total Assets, which is `BS_270`.
2. Query the `financial_statement` table fo

In [15]:
err

17

In [14]:
err_id

'69ecf8be-f65c-484c-87d6-069ff8fa530d'